In [ ]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_koc/cervix_koc_1737.jpg
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_koc/cervix_koc_3648.jpg
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_koc/cervix_koc_3082.jpg
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_koc/cervix_koc_4567.jpg
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_koc/cervix_koc_0955.jpg
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_koc/cervix_koc_1226.jpg
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_koc/cervix_koc_1326.jpg
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_koc/cervix_koc_0555.jpg
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_koc/cervix_koc_3821.jpg
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_koc/cervix_koc_1047.jpg
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_koc/cervix_koc_1968.jpg
/kaggle/input/multi-cancer/Multi Cancer/Cer

In [1]:
import numpy as np 
import pandas as pd
import os
import tensorflow as tf
from tensorflow import keras
from keras import Sequential
from keras.layers import Conv2D,MaxPooling2D,Dense,Dropout,Flatten,Input,InputLayer,GlobalAveragePooling1D,BatchNormalization
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from keras.optimizers import Adam

In [2]:
datasetPath="/kaggle/input"
for dirname,_,_ in os.walk(datasetPath): 
    print(dirname)

/kaggle/input
/kaggle/input/multi-cancer
/kaggle/input/multi-cancer/Multi Cancer
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_koc
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_dyk
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_pab
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_sfi
/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer/cervix_mep
/kaggle/input/multi-cancer/Multi Cancer/Lung and Colon Cancer
/kaggle/input/multi-cancer/Multi Cancer/Lung and Colon Cancer/colon_bnt
/kaggle/input/multi-cancer/Multi Cancer/Lung and Colon Cancer/colon_aca
/kaggle/input/multi-cancer/Multi Cancer/Lung and Colon Cancer/lung_aca
/kaggle/input/multi-cancer/Multi Cancer/Lung and Colon Cancer/lung_bnt
/kaggle/input/multi-cancer/Multi Cancer/Lung and Colon Cancer/lung_scc
/kaggle/input/multi-cancer/Multi Cancer/Oral Cancer
/kaggle/input/multi-cancer/Multi Cancer/Oral Cancer/oral_

In [3]:
imageShape=(224,224,3)

In [4]:
cervicalCancerPath="/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer"
lungCancerPath="/kaggle/input/multi-cancer/Multi Cancer/Lung and Colon Cancer"
oralCancerPath="/kaggle/input/multi-cancer/Multi Cancer/Oral Cancer"
ALLCancerPath="/kaggle/input/multi-cancer/Multi Cancer/ALL"
kidneyCancerPath="/kaggle/input/multi-cancer/Multi Cancer/Kidney Cancer"
breastCancerPath="/kaggle/input/multi-cancer/Multi Cancer/Breast Cancer"
lymphomaPath="/kaggle/input/multi-cancer/Multi Cancer/Lymphoma"
brainCancerPath="/kaggle/input/multi-cancer/Multi Cancer/Brain Cancer"

In [5]:
def initiateGenerator(dataset): 
    base_path = dataset
    train_dataset = tf.keras.preprocessing.image_dataset_from_directory(batch_size=32, directory=base_path)
    datagen = ImageDataGenerator(validation_split=0.2)
    
    # Generate the training data using the ImageDataGenerator
    print("\nFor Training : ", end=" ")
    train=datagen.flow_from_directory(
        dataset,
        target_size=(224,224),
        class_mode='categorical',
        batch_size=32,
        subset='training'
    )
    
    # Generate the validation data using the ImageDataGenerator
    print("\nFor Val : ", end=" ")
    validation=datagen.flow_from_directory(
        dataset,
        target_size=(224,224),
        class_mode='categorical',
        batch_size=32,
        subset='validation',
        shuffle=False
    )
    
    # Get the class names and number of classes in the dataset
    class_names = train_dataset.class_names
    noOfClasses = len(class_names)
#     noOfClasses=train_dataset.num_classes
    print("\nNo of Classes : ", noOfClasses)
    print("Classes : ", class_names)
    return train,validation,noOfClasses,class_names

In [6]:
from tensorflow.keras.regularizers import L2

In [7]:
def initiateModel(noOfClasses): 
    model = Sequential()

    # Input layer
    model.add(Input(shape=imageShape))

    # Add convolutional layers
    model.add(Conv2D(filters=16,kernel_size=3,padding='same',activation='relu'))
    model.add(MaxPooling2D(pool_size=(2, 2)))

    model.add(Conv2D(filters=32, kernel_size=3,padding='same', activation='relu'))
    model.add(MaxPooling2D(pool_size=(2, 2)))
    model.add(BatchNormalization())

    model.add(Conv2D(filters=64, kernel_size=3,padding='same', activation='relu'))
    model.add(MaxPooling2D(pool_size=(2, 2)))

    # Dropout layer
    model.add(Dropout(0.2))
    
    # Flatten the output
    model.add(Flatten())
    
    # Fully Connected Layers
    model.add(Dense(256, activation='relu'))

    # Output layer: use 'softmax' for multi-class classification, 'sigmoid' for binary classification
    model.add(Dense(noOfClasses, activation='softmax',kernel_regularizer=L2(0.001),bias_regularizer=L2(0.001)))
    return model

In [8]:
from keras.callbacks import EarlyStopping
earlystop= EarlyStopping(monitor='val_accuracy', patience=4,mode="max")

In [9]:
def modelCompile(model): 
    optimizer=keras.optimizers.Adam(learning_rate=0.0001)
    model.compile(optimizer=optimizer,loss='categorical_crossentropy',metrics=['accuracy'])

def modelFit(model,trainData,validation,epochs,batch_size): 
    steps_per_epoch = len(trainData) // batch_size  
    validation_steps = len(validation) // batch_size  
    history = model.fit(trainData,
                    validation_data=validation,
                    epochs=epochs,
                    verbose=1,steps_per_epoch=steps_per_epoch,batch_size=batch_size,
                       validation_steps=validation_steps,callbacks=[earlystop])

In [10]:
def modelSummary(model): 
    model.summary()

In [11]:
from keras.models import load_model

In [12]:
def savingModel(model, model_name="model"): 
    model_filename = f"{model_name}.h5"
    model.save(model_filename)
    print(f"Model saved as {model_filename}")

def loadingModel(model_name="model"): 
    try:
        model = load_model(f"{model_name}.h5")
        model.summary()  # Print model summary if needed
        return model  # Return the loaded model
    except Exception as e:
        print(f"Error loading model: {e}")
        return None

In [13]:
def loadImg(imgPath): 
    img = tf.keras.preprocessing.image.load_img(imgPath, target_size=(224, 224))
    img_array = tf.keras.preprocessing.image.img_to_array(img)
    img_array = np.expand_dims(img_array, axis=0)
    img_array=img_array/255.0
    return img_array

In [14]:
def predictImagesInFolder(testFolder, class_name, model_name): 
    savedModel = loadingModel(model_name)
    print(savedModel)

    if savedModel is None:
        print("Model loading failed.")
        return

    for subdir, dirs, files in os.walk(testFolder): 
        if subdir == testFolder: 
            continue
        trueLabel = os.path.basename(subdir)
        for file in files: 
            img_path = os.path.join(subdir, file)
            img = loadImg(img_path)
            
            # Debugging prediction probabilities
            predictions = savedModel.predict(img)
#             print(f"Prediction Probabilities for {file}: {predictions}")

            predicted_class_index = np.argmax(predictions, axis=1)
            predicted_class = class_name[predicted_class_index[0]]
            print(f"Predicted class: {predicted_class} File: {file}")


In [15]:
def testFolder(folder): 
    testFolder=f"{folder}"
    return testFolder

## Cervical Cancer Model

In [16]:
#      train,validation,noOfClasses,class_names
cervicalCancerTrainGenerator, cervicalCancerValidationGenerator, noOfClassesCervicalCancer, classNamesCervicalCancer = initiateGenerator(cervicalCancerPath)

Found 25000 files belonging to 5 classes.

For Training :  Found 20000 images belonging to 5 classes.

For Val :  Found 5000 images belonging to 5 classes.

No of Classes :  5
Classes :  ['cervix_dyk', 'cervix_koc', 'cervix_mep', 'cervix_pab', 'cervix_sfi']


In [17]:
noOfClassesCervicalCancer

5

In [18]:
cervicalCancerModel=initiateModel(noOfClassesCervicalCancer)

In [19]:
modelCompile(cervicalCancerModel)

In [20]:
modelSummary(cervicalCancerModel)

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d (Conv2D)                 │ (None, 224, 224, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d (MaxPooling2D)    │ (None, 112, 112, 16)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_1 (Conv2D)               │ (None, 112, 112, 32)   │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_1 (MaxPooling2D)  │ (None, 56, 56, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization             │ (None, 56, 56, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_2 (Conv2D)               │ (None, 56, 56, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_2 (MaxPooling2D)  │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten (Flatten)               │ (None, 50176)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 256)            │    12,845,312 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 5)              │         1,285 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,870,309 (49.10 MB)

 Trainable params: 12,870,245 (49.10 MB)

 Non-trainable params: 64 (256.00 B)

In [21]:
modelFit(cervicalCancerModel,cervicalCancerTrainGenerator,cervicalCancerValidationGenerator,50,32)

Epoch 1/50


/opt/conda/lib/python3.10/site-packages/keras/src/trainers/data_adapters/py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


19/19 ━━━━━━━━━━━━━━━━━━━━ 25s 1s/step - accuracy: 0.3885 - loss: 2.3691 - val_accuracy: 0.0000e+00 - val_loss: 11.3103
Epoch 2/50
19/19 ━━━━━━━━━━━━━━━━━━━━ 19s 980ms/step - accuracy: 0.6400 - loss: 0.9560 - val_accuracy: 0.0000e+00 - val_loss: 6.3758
Epoch 3/50
19/19 ━━━━━━━━━━━━━━━━━━━━ 18s 945ms/step - accuracy: 0.6585 - loss: 0.8557 - val_accuracy: 0.0078 - val_loss: 5.0182
Epoch 4/50
19/19 ━━━━━━━━━━━━━━━━━━━━ 19s 974ms/step - accuracy: 0.7193 - loss: 0.7314 - val_accuracy: 0.0469 - val_loss: 3.5944
Epoch 5/50
19/19 ━━━━━━━━━━━━━━━━━━━━ 18s 942ms/step - accuracy: 0.7829 - loss: 0.6747 - val_accuracy: 0.0781 - val_loss: 3.3614
Epoch 6/50
19/19 ━━━━━━━━━━━━━━━━━━━━ 18s 973ms/step - accuracy: 0.7568 - loss: 0.6558 - val_accuracy: 0.5625 - val_loss: 0.8693
Epoch 7/50
19/19 ━━━━━━━━━━━━━━━━━━━━ 18s 948ms/step - accuracy: 0.7497 - loss: 0.6581 - val_accuracy: 0.3594 - val_loss: 1.6570
Epoch 8/50
19/19 ━━━━━━━━━━━━━━━━━━━━ 18s 974ms/step - accuracy: 0.7815 - loss: 0.6001 - val_accuracy:

In [22]:
cervicalCancerTrainGenerator.class_indices

{'cervix_dyk': 0,
 'cervix_koc': 1,
 'cervix_mep': 2,
 'cervix_pab': 3,
 'cervix_sfi': 4}

In [23]:
savingModel(cervicalCancerModel,model_name="CervicalCancerModel")

Model saved as CervicalCancerModel.h5


In [24]:
loadedModel=loadingModel("CervicalCancerModel")

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d (Conv2D)                 │ (None, 224, 224, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d (MaxPooling2D)    │ (None, 112, 112, 16)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_1 (Conv2D)               │ (None, 112, 112, 32)   │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_1 (MaxPooling2D)  │ (None, 56, 56, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization             │ (None, 56, 56, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_2 (Conv2D)               │ (None, 56, 56, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_2 (MaxPooling2D)  │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten (Flatten)               │ (None, 50176)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 256)            │    12,845,312 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 5)              │         1,285 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,870,311 (49.10 MB)

 Trainable params: 12,870,245 (49.10 MB)

 Non-trainable params: 64 (256.00 B)

 Optimizer params: 2 (12.00 B)

In [25]:
cervicalTestFolder=testFolder(cervicalCancerPath)

In [26]:
print(cervicalTestFolder)

/kaggle/input/multi-cancer/Multi Cancer/Cervical Cancer


In [27]:
class_name={
    0:'cervix_dyk',
    1:'cervix_koc',
    2:'cervix_mep',
    3:'cervix_pab',
    4:'cervix_sfi'
}

In [28]:
predictImagesInFolder(cervicalTestFolder,class_name, model_name="CervicalCancerModel")

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d (Conv2D)                 │ (None, 224, 224, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d (MaxPooling2D)    │ (None, 112, 112, 16)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_1 (Conv2D)               │ (None, 112, 112, 32)   │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_1 (MaxPooling2D)  │ (None, 56, 56, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization             │ (None, 56, 56, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_2 (Conv2D)               │ (None, 56, 56, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_2 (MaxPooling2D)  │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten (Flatten)               │ (None, 50176)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 256)            │    12,845,312 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 5)              │         1,285 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,870,311 (49.10 MB)

 Trainable params: 12,870,245 (49.10 MB)

 Non-trainable params: 64 (256.00 B)

 Optimizer params: 2 (12.00 B)

<Sequential name=sequential, built=True>
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 113ms/step
Predicted class: cervix_koc File: cervix_koc_1737.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: cervix_koc File: cervix_koc_3648.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
Predicted class: cervix_koc File: cervix_koc_3082.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: cervix_koc File: cervix_koc_4567.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: cervix_koc File: cervix_koc_0955.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: cervix_koc File: cervix_koc_1226.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: cervix_koc File: cervix_koc_1326.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: cervix_koc File: cervix_koc_0555.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: cervix_koc File: cervix_koc_3821.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: cervix_koc File: cervix_koc_1047.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step


RuntimeError: Exiting device scope without proper scope nesting

## Oral Cancer Model

In [29]:
# oralCancerTrain.class_indices
oralCancerTrainGenerator, oralCancerValidationGenerator, noOfClassesOralCancer, classNamesOralCancer = initiateGenerator(oralCancerPath)

Found 10002 files belonging to 2 classes.

For Training :  Found 8002 images belonging to 2 classes.

For Val :  Found 2000 images belonging to 2 classes.

No of Classes :  2
Classes :  ['oral_normal', 'oral_scc']


In [30]:
oralCancerClassName={
    0: 'oral_normal',
    1: 'oral_scc'
}

In [31]:
oralCancerModel = initiateModel(noOfClassesOralCancer)
modelCompile(oralCancerModel)

In [32]:
modelSummary(oralCancerModel)

Model: "sequential_1"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d_3 (Conv2D)               │ (None, 224, 224, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_3 (MaxPooling2D)  │ (None, 112, 112, 16)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_4 (Conv2D)               │ (None, 112, 112, 32)   │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_4 (MaxPooling2D)  │ (None, 56, 56, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_1           │ (None, 56, 56, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_5 (Conv2D)               │ (None, 56, 56, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_5 (MaxPooling2D)  │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_1 (Dropout)             │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_1 (Flatten)             │ (None, 50176)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_2 (Dense)                 │ (None, 256)            │    12,845,312 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_3 (Dense)                 │ (None, 2)              │           514 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,869,538 (49.09 MB)

 Trainable params: 12,869,474 (49.09 MB)

 Non-trainable params: 64 (256.00 B)

In [33]:
modelFit(oralCancerModel,oralCancerTrainGenerator,oralCancerValidationGenerator,50,8)

Epoch 1/50
31/31 ━━━━━━━━━━━━━━━━━━━━ 37s 1s/step - accuracy: 0.5370 - loss: 1.7888 - val_accuracy: 1.0000 - val_loss: 0.0799
Epoch 2/50
31/31 ━━━━━━━━━━━━━━━━━━━━ 30s 977ms/step - accuracy: 0.6366 - loss: 0.6413 - val_accuracy: 0.9955 - val_loss: 0.2453
Epoch 3/50
31/31 ━━━━━━━━━━━━━━━━━━━━ 29s 951ms/step - accuracy: 0.6445 - loss: 0.6083 - val_accuracy: 1.0000 - val_loss: 0.2977
Epoch 4/50
31/31 ━━━━━━━━━━━━━━━━━━━━ 30s 970ms/step - accuracy: 0.6870 - loss: 0.5907 - val_accuracy: 1.0000 - val_loss: 0.1937
Epoch 5/50
31/31 ━━━━━━━━━━━━━━━━━━━━ 30s 959ms/step - accuracy: 0.6654 - loss: 0.6165 - val_accuracy: 0.6161 - val_loss: 0.6335


In [34]:
oralTestFolder=testFolder(oralCancerPath)

In [35]:
oralTestFolder

'/kaggle/input/multi-cancer/Multi Cancer/Oral Cancer'

In [36]:
savingModel(oralCancerModel,model_name="OralCancerModel")

Model saved as OralCancerModel.h5


In [37]:
loadedModel=loadingModel("OralCancerModel")

Model: "sequential_1"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d_3 (Conv2D)               │ (None, 224, 224, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_3 (MaxPooling2D)  │ (None, 112, 112, 16)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_4 (Conv2D)               │ (None, 112, 112, 32)   │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_4 (MaxPooling2D)  │ (None, 56, 56, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_1           │ (None, 56, 56, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_5 (Conv2D)               │ (None, 56, 56, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_5 (MaxPooling2D)  │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_1 (Dropout)             │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_1 (Flatten)             │ (None, 50176)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_2 (Dense)                 │ (None, 256)            │    12,845,312 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_3 (Dense)                 │ (None, 2)              │           514 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,869,540 (49.09 MB)

 Trainable params: 12,869,474 (49.09 MB)

 Non-trainable params: 64 (256.00 B)

 Optimizer params: 2 (12.00 B)

In [38]:
predictImagesInFolder(oralTestFolder,oralCancerClassName, model_name="OralCancerModel")

Model: "sequential_1"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d_3 (Conv2D)               │ (None, 224, 224, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_3 (MaxPooling2D)  │ (None, 112, 112, 16)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_4 (Conv2D)               │ (None, 112, 112, 32)   │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_4 (MaxPooling2D)  │ (None, 56, 56, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_1           │ (None, 56, 56, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_5 (Conv2D)               │ (None, 56, 56, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_5 (MaxPooling2D)  │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_1 (Dropout)             │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_1 (Flatten)             │ (None, 50176)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_2 (Dense)                 │ (None, 256)            │    12,845,312 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_3 (Dense)                 │ (None, 2)              │           514 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,869,540 (49.09 MB)

 Trainable params: 12,869,474 (49.09 MB)

 Non-trainable params: 64 (256.00 B)

 Optimizer params: 2 (12.00 B)

<Sequential name=sequential_1, built=True>
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 107ms/step
Predicted class: oral_scc File: oral_scc_0771.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: oral_scc File: oral_scc_0707.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: oral_scc File: oral_scc_3093.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
Predicted class: oral_scc File: oral_scc_0480.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: oral_scc File: oral_scc_0654.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: oral_scc File: oral_scc_0620.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: oral_scc File: oral_scc_3567.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: oral_scc File: oral_scc_1208.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
Predicted class: oral_scc File: oral_scc_0761.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: oral_scc File: oral_scc_2566.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: oral_scc File: oral_s

KeyboardInterrupt: 

## ALL 

In [39]:
ALLCancerTrainGenerator, ALLCancerValidationGenerator, noOfClassesALLCancer, classNamesALLCancer = initiateGenerator(ALLCancerPath)

Found 20000 files belonging to 4 classes.

For Training :  Found 16000 images belonging to 4 classes.

For Val :  Found 4000 images belonging to 4 classes.

No of Classes :  4
Classes :  ['all_benign', 'all_early', 'all_pre', 'all_pro']


In [40]:
ALLCancerTrainGenerator.class_indices

{'all_benign': 0, 'all_early': 1, 'all_pre': 2, 'all_pro': 3}

In [41]:
ALLCancerClassName={0: 'all_benign', 1:'all_early' , 2:'all_pre', 3:'all_pro'}

In [42]:
ALLCancerModel = initiateModel(noOfClassesALLCancer)
modelCompile(ALLCancerModel)

In [43]:
modelSummary(ALLCancerModel)

Model: "sequential_2"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d_6 (Conv2D)               │ (None, 224, 224, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_6 (MaxPooling2D)  │ (None, 112, 112, 16)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_7 (Conv2D)               │ (None, 112, 112, 32)   │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_7 (MaxPooling2D)  │ (None, 56, 56, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_2           │ (None, 56, 56, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_8 (Conv2D)               │ (None, 56, 56, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_8 (MaxPooling2D)  │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_2 (Dropout)             │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_2 (Flatten)             │ (None, 50176)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_4 (Dense)                 │ (None, 256)            │    12,845,312 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_5 (Dense)                 │ (None, 4)              │         1,028 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,870,052 (49.10 MB)

 Trainable params: 12,869,988 (49.10 MB)

 Non-trainable params: 64 (256.00 B)

In [47]:
modelFit(ALLCancerModel,ALLCancerTrainGenerator,ALLCancerValidationGenerator,50,8)

Epoch 1/50
62/62 ━━━━━━━━━━━━━━━━━━━━ 60s 938ms/step - accuracy: 0.8779 - loss: 0.3639 - val_accuracy: 0.1750 - val_loss: 2.8578
Epoch 2/50
62/62 ━━━━━━━━━━━━━━━━━━━━ 58s 939ms/step - accuracy: 0.9328 - loss: 0.2066 - val_accuracy: 0.7937 - val_loss: 0.5143
Epoch 3/50
62/62 ━━━━━━━━━━━━━━━━━━━━ 59s 957ms/step - accuracy: 0.9515 - loss: 0.1624 - val_accuracy: 0.9812 - val_loss: 0.1087
Epoch 4/50
62/62 ━━━━━━━━━━━━━━━━━━━━ 59s 951ms/step - accuracy: 0.9515 - loss: 0.1549 - val_accuracy: 0.9833 - val_loss: 0.0622


In [48]:
ALLTestFolder=testFolder(ALLCancerPath)
ALLTestFolder

'/kaggle/input/multi-cancer/Multi Cancer/ALL'

In [49]:
savingModel(ALLCancerModel,model_name="ALLCancerModel")

Model saved as ALLCancerModel.h5


In [50]:
loadedModel=loadingModel("ALLCancerModel")

Model: "sequential_2"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d_6 (Conv2D)               │ (None, 224, 224, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_6 (MaxPooling2D)  │ (None, 112, 112, 16)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_7 (Conv2D)               │ (None, 112, 112, 32)   │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_7 (MaxPooling2D)  │ (None, 56, 56, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_2           │ (None, 56, 56, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_8 (Conv2D)               │ (None, 56, 56, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_8 (MaxPooling2D)  │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_2 (Dropout)             │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_2 (Flatten)             │ (None, 50176)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_4 (Dense)                 │ (None, 256)            │    12,845,312 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_5 (Dense)                 │ (None, 4)              │         1,028 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,870,054 (49.10 MB)

 Trainable params: 12,869,988 (49.10 MB)

 Non-trainable params: 64 (256.00 B)

 Optimizer params: 2 (12.00 B)

In [51]:
predictImagesInFolder(ALLTestFolder,ALLCancerClassName, model_name="ALLCancerModel")

Model: "sequential_2"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d_6 (Conv2D)               │ (None, 224, 224, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_6 (MaxPooling2D)  │ (None, 112, 112, 16)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_7 (Conv2D)               │ (None, 112, 112, 32)   │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_7 (MaxPooling2D)  │ (None, 56, 56, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_2           │ (None, 56, 56, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_8 (Conv2D)               │ (None, 56, 56, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_8 (MaxPooling2D)  │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_2 (Dropout)             │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_2 (Flatten)             │ (None, 50176)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_4 (Dense)                 │ (None, 256)            │    12,845,312 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_5 (Dense)                 │ (None, 4)              │         1,028 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,870,054 (49.10 MB)

 Trainable params: 12,869,988 (49.10 MB)

 Non-trainable params: 64 (256.00 B)

 Optimizer params: 2 (12.00 B)

<Sequential name=sequential_2, built=True>
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 104ms/step
Predicted class: all_benign File: all_pro_0428.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: all_benign File: all_pro_1384.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
Predicted class: all_benign File: all_pro_1665.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: all_benign File: all_pro_2095.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: all_benign File: all_pro_3631.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: all_benign File: all_pro_3249.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: all_benign File: all_pro_4764.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: all_benign File: all_pro_1253.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: all_benign File: all_pro_4035.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: all_benign File: all_pro_2600.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: all_benign 

KeyboardInterrupt: 

## Brain Cancer

In [52]:
brainCancerTrainGenerator, brainCancerValidationGenerator, noOfClassesBrainCancer, classNamesBrainCancer = initiateGenerator(brainCancerPath)

Found 15000 files belonging to 3 classes.

For Training :  Found 12000 images belonging to 3 classes.

For Val :  Found 3000 images belonging to 3 classes.

No of Classes :  3
Classes :  ['brain_glioma', 'brain_menin', 'brain_tumor']


In [53]:
brainCancerClassName={0: 'brain_glioma', 1:'brain_menin' , 2:'brain_tumor'}

In [54]:
brainCancerModel = initiateModel(noOfClassesBrainCancer)
modelCompile(brainCancerModel)

In [55]:
modelCompile(brainCancerModel)

In [56]:
modelFit(brainCancerModel,brainCancerTrainGenerator,brainCancerValidationGenerator,10,8)

Epoch 1/10
46/46 ━━━━━━━━━━━━━━━━━━━━ 49s 972ms/step - accuracy: 0.5167 - loss: 2.0355 - val_accuracy: 0.0028 - val_loss: 4.7267
Epoch 2/10
46/46 ━━━━━━━━━━━━━━━━━━━━ 44s 948ms/step - accuracy: 0.7293 - loss: 0.6732 - val_accuracy: 0.0597 - val_loss: 2.7251
Epoch 3/10
46/46 ━━━━━━━━━━━━━━━━━━━━ 43s 946ms/step - accuracy: 0.7700 - loss: 0.5699 - val_accuracy: 0.4631 - val_loss: 1.1272
Epoch 4/10
46/46 ━━━━━━━━━━━━━━━━━━━━ 43s 937ms/step - accuracy: 0.7809 - loss: 0.5523 - val_accuracy: 0.7159 - val_loss: 0.7078


In [57]:
brainCancerTestFolder=testFolder(brainCancerPath)
brainCancerTestFolder

'/kaggle/input/multi-cancer/Multi Cancer/Brain Cancer'

In [58]:
savingModel(brainCancerModel,model_name="brainCancerModel")

Model saved as brainCancerModel.h5


In [59]:
loadedModel=loadingModel("brainCancerModel")

Model: "sequential_3"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d_9 (Conv2D)               │ (None, 224, 224, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_9 (MaxPooling2D)  │ (None, 112, 112, 16)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_10 (Conv2D)              │ (None, 112, 112, 32)   │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_10 (MaxPooling2D) │ (None, 56, 56, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_3           │ (None, 56, 56, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_11 (Conv2D)              │ (None, 56, 56, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_11 (MaxPooling2D) │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_3 (Dropout)             │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_3 (Flatten)             │ (None, 50176)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_6 (Dense)                 │ (None, 256)            │    12,845,312 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_7 (Dense)                 │ (None, 3)              │           771 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,869,797 (49.09 MB)

 Trainable params: 12,869,731 (49.09 MB)

 Non-trainable params: 64 (256.00 B)

 Optimizer params: 2 (12.00 B)

In [60]:
predictImagesInFolder(brainCancerTestFolder,brainCancerClassName, model_name="brainCancerModel")

Model: "sequential_3"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d_9 (Conv2D)               │ (None, 224, 224, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_9 (MaxPooling2D)  │ (None, 112, 112, 16)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_10 (Conv2D)              │ (None, 112, 112, 32)   │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_10 (MaxPooling2D) │ (None, 56, 56, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_3           │ (None, 56, 56, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_11 (Conv2D)              │ (None, 56, 56, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_11 (MaxPooling2D) │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_3 (Dropout)             │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_3 (Flatten)             │ (None, 50176)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_6 (Dense)                 │ (None, 256)            │    12,845,312 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_7 (Dense)                 │ (None, 3)              │           771 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,869,797 (49.09 MB)

 Trainable params: 12,869,731 (49.09 MB)

 Non-trainable params: 64 (256.00 B)

 Optimizer params: 2 (12.00 B)

<Sequential name=sequential_3, built=True>
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 103ms/step
Predicted class: brain_glioma File: brain_tumor_4683.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
Predicted class: brain_glioma File: brain_tumor_2205.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: brain_glioma File: brain_tumor_2421.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: brain_glioma File: brain_tumor_2869.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
Predicted class: brain_glioma File: brain_tumor_2386.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
Predicted class: brain_glioma File: brain_tumor_1402.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: brain_glioma File: brain_tumor_2858.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
Predicted class: brain_glioma File: brain_tumor_0483.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: brain_glioma File: brain_tumor_0141.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
Predicted class: brain_glioma File: brain_tumor_4012.jpg
1/1 ━━

KeyboardInterrupt: 

## Lymphoma

In [61]:
lymphomaCancerTrainGenerator, lymphomaCancerValidationGenerator, noOfClassesLymphomaCancer, classNamesLymphomaCancer = initiateGenerator(lymphomaPath)

Found 15000 files belonging to 3 classes.

For Training :  Found 12000 images belonging to 3 classes.

For Val :  Found 3000 images belonging to 3 classes.

No of Classes :  3
Classes :  ['lymph_cll', 'lymph_fl', 'lymph_mcl']


In [62]:
lymphomaCancerClassName={0:'lymph_cll', 1:'lymph_fl', 2:'lymph_mcl'}

In [63]:
lymphomaCancerModel = initiateModel(noOfClassesLymphomaCancer)
modelCompile(lymphomaCancerModel)

In [65]:
modelFit(lymphomaCancerModel,lymphomaCancerTrainGenerator,lymphomaCancerValidationGenerator,10,8)

Epoch 1/10


/opt/conda/lib/python3.10/site-packages/keras/src/trainers/data_adapters/py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


46/46 ━━━━━━━━━━━━━━━━━━━━ 52s 1s/step - accuracy: 0.4028 - loss: 3.7891 - val_accuracy: 0.0000e+00 - val_loss: 2.8918
Epoch 2/10
46/46 ━━━━━━━━━━━━━━━━━━━━ 46s 1s/step - accuracy: 0.5326 - loss: 0.9665 - val_accuracy: 0.0000e+00 - val_loss: 3.7483
Epoch 3/10
46/46 ━━━━━━━━━━━━━━━━━━━━ 45s 982ms/step - accuracy: 0.5563 - loss: 0.8843 - val_accuracy: 0.2273 - val_loss: 1.1255
Epoch 4/10
46/46 ━━━━━━━━━━━━━━━━━━━━ 46s 999ms/step - accuracy: 0.5566 - loss: 0.9909 - val_accuracy: 0.9432 - val_loss: 0.3017


In [67]:
lymphomaCancerTestFolder=testFolder(lymphomaPath)
lymphomaCancerTestFolder

'/kaggle/input/multi-cancer/Multi Cancer/Lymphoma'

In [68]:
savingModel(lymphomaCancerModel,model_name="lymphomaModel")

Model saved as lymphomaModel.h5


In [69]:
loadedModel=loadingModel("lymphomaModel")

Model: "sequential_4"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d_12 (Conv2D)              │ (None, 224, 224, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_12 (MaxPooling2D) │ (None, 112, 112, 16)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_13 (Conv2D)              │ (None, 112, 112, 32)   │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_13 (MaxPooling2D) │ (None, 56, 56, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_4           │ (None, 56, 56, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_14 (Conv2D)              │ (None, 56, 56, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_14 (MaxPooling2D) │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_4 (Dropout)             │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_4 (Flatten)             │ (None, 50176)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_8 (Dense)                 │ (None, 256)            │    12,845,312 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_9 (Dense)                 │ (None, 3)              │           771 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,869,797 (49.09 MB)

 Trainable params: 12,869,731 (49.09 MB)

 Non-trainable params: 64 (256.00 B)

 Optimizer params: 2 (12.00 B)

In [70]:
predictImagesInFolder(lymphomaCancerTestFolder,lymphomaCancerClassName, model_name="lymphomaModel")

Model: "sequential_4"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d_12 (Conv2D)              │ (None, 224, 224, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_12 (MaxPooling2D) │ (None, 112, 112, 16)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_13 (Conv2D)              │ (None, 112, 112, 32)   │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_13 (MaxPooling2D) │ (None, 56, 56, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_4           │ (None, 56, 56, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_14 (Conv2D)              │ (None, 56, 56, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_14 (MaxPooling2D) │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_4 (Dropout)             │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_4 (Flatten)             │ (None, 50176)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_8 (Dense)                 │ (None, 256)            │    12,845,312 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_9 (Dense)                 │ (None, 3)              │           771 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,869,797 (49.09 MB)

 Trainable params: 12,869,731 (49.09 MB)

 Non-trainable params: 64 (256.00 B)

 Optimizer params: 2 (12.00 B)

<Sequential name=sequential_4, built=True>
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 125ms/step
Predicted class: lymph_fl File: lymph_fl_2906.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
Predicted class: lymph_fl File: lymph_fl_0607.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
Predicted class: lymph_fl File: lymph_fl_1911.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
Predicted class: lymph_fl File: lymph_fl_4691.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: lymph_fl File: lymph_fl_1990.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: lymph_fl File: lymph_fl_4911.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
Predicted class: lymph_fl File: lymph_fl_4946.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
Predicted class: lymph_fl File: lymph_fl_3588.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
Predicted class: lymph_fl File: lymph_fl_0635.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
Predicted class: lymph_fl File: lymph_fl_2705.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: lymph_fl File: lymph_

KeyboardInterrupt: 

## Lung and Colon Cancer

In [82]:
lungCancerTrainGenerator, lungCancerValidationGenerator, noOfClassesLungCancer, classNamesLungCancer = initiateGenerator(lungCancerPath)

Found 25000 files belonging to 5 classes.

For Training :  Found 20000 images belonging to 5 classes.

For Val :  Found 5000 images belonging to 5 classes.

No of Classes :  5
Classes :  ['colon_aca', 'colon_bnt', 'lung_aca', 'lung_bnt', 'lung_scc']


In [83]:
lungCancerClassName={0:'colon_aca', 1:'colon_bnt', 2:'lung_aca',3:'lung_bnt',4:'lung_scc'}

In [84]:
lungCancerModel = initiateModel(noOfClassesLungCancer)
modelCompile(lungCancerModel)

In [85]:
# modelFit(lymphomaCancerModel,lymphomaCancerTrainGenerator,lymphomaCancerValidationGenerator,10,8)
modelFit(lungCancerModel,lungCancerTrainGenerator,lungCancerValidationGenerator,100,16)

Epoch 1/100


/opt/conda/lib/python3.10/site-packages/keras/src/trainers/data_adapters/py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


39/39 ━━━━━━━━━━━━━━━━━━━━ 44s 1s/step - accuracy: 0.4827 - loss: 1.9450 - val_accuracy: 1.0000 - val_loss: 0.0095
Epoch 2/100
39/39 ━━━━━━━━━━━━━━━━━━━━ 38s 987ms/step - accuracy: 0.7135 - loss: 0.6451 - val_accuracy: 0.9931 - val_loss: 0.1308
Epoch 3/100
39/39 ━━━━━━━━━━━━━━━━━━━━ 38s 986ms/step - accuracy: 0.8079 - loss: 0.4360 - val_accuracy: 0.1076 - val_loss: 2.1123
Epoch 4/100
39/39 ━━━━━━━━━━━━━━━━━━━━ 39s 991ms/step - accuracy: 0.7533 - loss: 0.5596 - val_accuracy: 0.8090 - val_loss: 0.4699


In [86]:
lungCancerTestFolder=testFolder(lungCancerPath)
lungCancerTestFolder

'/kaggle/input/multi-cancer/Multi Cancer/Lung and Colon Cancer'

In [87]:
savingModel(lungCancerModel,model_name="lungModel")

Model saved as lungModel.h5


In [88]:
loadedModel=loadingModel("lungModel")

Model: "sequential_6"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d_18 (Conv2D)              │ (None, 224, 224, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_18 (MaxPooling2D) │ (None, 112, 112, 16)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_19 (Conv2D)              │ (None, 112, 112, 32)   │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_19 (MaxPooling2D) │ (None, 56, 56, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_6           │ (None, 56, 56, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_20 (Conv2D)              │ (None, 56, 56, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_20 (MaxPooling2D) │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_6 (Dropout)             │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_6 (Flatten)             │ (None, 50176)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_12 (Dense)                │ (None, 256)            │    12,845,312 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_13 (Dense)                │ (None, 5)              │         1,285 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,870,311 (49.10 MB)

 Trainable params: 12,870,245 (49.10 MB)

 Non-trainable params: 64 (256.00 B)

 Optimizer params: 2 (12.00 B)

In [90]:
predictImagesInFolder(lungCancerTestFolder,lungCancerClassName, model_name="lungModel")

Model: "sequential_6"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d_18 (Conv2D)              │ (None, 224, 224, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_18 (MaxPooling2D) │ (None, 112, 112, 16)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_19 (Conv2D)              │ (None, 112, 112, 32)   │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_19 (MaxPooling2D) │ (None, 56, 56, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_6           │ (None, 56, 56, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_20 (Conv2D)              │ (None, 56, 56, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_20 (MaxPooling2D) │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_6 (Dropout)             │ (None, 28, 28, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_6 (Flatten)             │ (None, 50176)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_12 (Dense)                │ (None, 256)            │    12,845,312 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_13 (Dense)                │ (None, 5)              │         1,285 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 12,870,311 (49.10 MB)

 Trainable params: 12,870,245 (49.10 MB)

 Non-trainable params: 64 (256.00 B)

 Optimizer params: 2 (12.00 B)

<Sequential name=sequential_6, built=True>
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 133ms/step
Predicted class: lung_bnt File: colon_bnt_2883.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
Predicted class: lung_bnt File: colon_bnt_4609.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: lung_bnt File: colon_bnt_3018.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
Predicted class: lung_bnt File: colon_bnt_4065.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
Predicted class: lung_bnt File: colon_bnt_0163.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
Predicted class: lung_bnt File: colon_bnt_4888.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
Predicted class: lung_bnt File: colon_bnt_0253.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: lung_bnt File: colon_bnt_2363.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
Predicted class: lung_bnt File: colon_bnt_0910.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: lung_bnt File: colon_bnt_2072.jpg
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
Predicted class: lung_bnt Fi

KeyboardInterrupt: 